# Install and import libraries

In [ ]:
!pip install faiss-cpu sentence-transformers tqdm transformers accelerate

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 30.7/30.7 MB 65.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 2.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 109.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 82.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 59.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 37.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 5.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 4.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 98.8 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitlink-cu12
    Found existing installation: nvidia-nvjitlink-cu12 12.5.82
    Uninstalli

In [ ]:
import os
import json
import glob
import numpy as np
import pandas as pd
import torch
import faiss
import tqdm
import gc
from typing import List, Dict, Any, Tuple, Optional
from dataclasses import dataclass
from transformers import LlamaForCausalLM, LlamaTokenizer, AutoTokenizer, AutoModel
from sentence_transformers import SentenceTransformer
from torch.utils.data import Dataset, DataLoader

# Configuration

In [ ]:
# from google.colab import drive
# drive.mount('/content/drive')
# %cd /content/drive/MyDrive/MSDS490_Project
# import os
# print(os.getcwd())

In [ ]:
# Set device configuration
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

# Memory management utility functions
def clear_gpu_memory():
    """Clear GPU memory to free up resources."""
    torch.cuda.empty_cache()
    gc.collect()

def get_gpu_memory_usage():
    """Return GPU memory usage in MB."""
    if torch.cuda.is_available():
        return torch.cuda.memory_allocated() / 1024**2
    return 0

Using device: cuda


# Main Code

## Document Class

In [ ]:
@dataclass
class Document:
    """Class to represent a document in the RAG system."""
    text: str
    metadata: Dict[str, Any]

## Financial Data Loader

In [ ]:
class FinancialDataLoader:
    """Load and preprocess financial data from various sources."""

    def __init__(self, base_dir: str):
        """Initialize the data loader.

        Args:
            base_dir: Base directory containing the data folders
        """
        self.base_dir = base_dir
        self.tenk_dir = os.path.join(base_dir, "10-K")
        self.pr_dir = os.path.join(base_dir, "PR")
        self.earnings_dir = os.path.join(base_dir, "Earnings_Transcripts")
        self.sec_dir = os.path.join(base_dir, "SEC_Data")

        # Get all company folders
        self.companies = set()
        for directory in [self.tenk_dir, self.pr_dir, self.earnings_dir, self.sec_dir]:
            if os.path.exists(directory):
                self.companies.update([os.path.basename(f) for f in glob.glob(os.path.join(directory, "*"))
                                      if os.path.isdir(f)])
        print(f"Found {len(self.companies)} companies: {', '.join(self.companies)}")

    def load_10k_data(self) -> List[Document]:
        """Load 10-K report data."""
        documents = []

        print("Loading 10-K data...")
        for company in tqdm.tqdm(self.companies):
            company_dir = os.path.join(self.tenk_dir, company)
            if not os.path.exists(company_dir):
                continue

            for file_path in glob.glob(os.path.join(company_dir, "*.json")):
                try:
                    with open(file_path, 'r') as f:
                        data = json.load(f)

                    # Extract filename components for metadata
                    filename = os.path.basename(file_path)

                    # Process each chunk in the file
                    if isinstance(data, list):
                        for i, chunk in enumerate(data):
                            if isinstance(chunk, dict) and 'text' in chunk:
                                doc = Document(
                                    text=chunk['text'],
                                    metadata={
                                        'source': '10-K',
                                        'company': company,
                                        'file': filename,
                                        'chunk_id': i,
                                        **{k: v for k, v in chunk.items() if k != 'text'}
                                    }
                                )
                                documents.append(doc)
                    elif isinstance(data, dict) and 'text' in data:
                        doc = Document(
                            text=data['text'],
                            metadata={
                                'source': '10-K',
                                'company': company,
                                'file': filename,
                                **{k: v for k, v in data.items() if k != 'text'}
                            }
                        )
                        documents.append(doc)
                except Exception as e:
                    print(f"Error loading 10-K file {file_path}: {e}")

        print(f"Loaded {len(documents)} 10-K document chunks")
        return documents

    def load_pr_data(self) -> List[Document]:
        """Load press release data."""
        documents = []

        print("Loading press release data...")
        for company in tqdm.tqdm(self.companies):
            company_dir = os.path.join(self.pr_dir, company)
            if not os.path.exists(company_dir):
                continue

            for file_path in glob.glob(os.path.join(company_dir, "*")):
                try:
                    # For raw text files
                    with open(file_path, 'r', encoding='utf-8', errors='ignore') as f:
                        content = f.read()

                    # Extract date from filename if possible (assuming format like YYYY-MM-DD or similar)
                    filename = os.path.basename(file_path)

                    # Create document
                    doc = Document(
                        text=content,
                        metadata={
                            'source': 'Press Release',
                            'company': company,
                            'file': filename
                        }
                    )
                    documents.append(doc)
                except Exception as e:
                    print(f"Error loading PR file {file_path}: {e}")

        print(f"Loaded {len(documents)} press release documents")
        return documents

    def load_earnings_data(self) -> List[Document]:
        """Load earnings transcript data."""
        documents = []

        print("Loading earnings transcript data...")
        for company in tqdm.tqdm(self.companies):
            company_dir = os.path.join(self.earnings_dir, company)
            if not os.path.exists(company_dir):
                continue

            for file_path in glob.glob(os.path.join(company_dir, "*.json")):
                try:
                    with open(file_path, 'r') as f:
                        data = json.load(f)

                    # Extract filename components for metadata
                    filename = os.path.basename(file_path)

                    # Process each chunk in the file
                    if isinstance(data, list):
                        for i, chunk in enumerate(data):
                            if isinstance(chunk, dict) and 'text' in chunk:
                                doc = Document(
                                    text=chunk['text'],
                                    metadata={
                                        'source': 'Earnings Transcript',
                                        'company': company,
                                        'file': filename,
                                        'chunk_id': i,
                                        **{k: v for k, v in chunk.items() if k != 'text'}
                                    }
                                )
                                documents.append(doc)
                    elif isinstance(data, dict) and 'text' in data:
                        doc = Document(
                            text=data['text'],
                            metadata={
                                'source': 'Earnings Transcript',
                                'company': company,
                                'file': filename,
                                **{k: v for k, v in data.items() if k != 'text'}
                            }
                        )
                        documents.append(doc)
                except Exception as e:
                    print(f"Error loading earnings file {file_path}: {e}")

        print(f"Loaded {len(documents)} earnings transcript chunks")
        return documents

    def load_sec_data(self) -> List[Document]:
        """Load SEC financial metric data."""
        documents = []

        print("Loading SEC financial data...")
        for company in tqdm.tqdm(self.companies):
            company_dir = os.path.join(self.sec_dir, company)
            if not os.path.exists(company_dir):
                continue

            for file_path in glob.glob(os.path.join(company_dir, "*.json")):
                try:
                    with open(file_path, 'r') as f:
                        data = json.load(f)

                    # For financial metrics, transform the JSON into a more readable text format
                    # so it can be embedded and retrieved effectively
                    if isinstance(data, dict):
                        for metric, values in data.items():
                            if isinstance(values, list) and len(values) > 0:
                                # Group by year for better context
                                by_year = {}
                                for entry in values:
                                    if 'end' in entry and 'val' in entry:
                                        year = entry['end'].split('-')[0]
                                        if year not in by_year:
                                            by_year[year] = []
                                        by_year[year].append(entry)

                                for year, entries in by_year.items():
                                    # Format the financial data as text
                                    text_content = f"Financial Metric: {metric} for {company} in {year}\n\n"
                                    for entry in entries:
                                        date = entry.get('end', 'N/A')
                                        value = entry.get('val', 'N/A')
                                        form = entry.get('form', 'N/A')
                                        filed = entry.get('filed', 'N/A')

                                        text_content += f"As of {date}, {metric} was {value:,} "
                                        text_content += f"reported in {form} filed on {filed}.\n"

                                    doc = Document(
                                        text=text_content,
                                        metadata={
                                            'source': 'SEC Financial Data',
                                            'company': company,
                                            'metric': metric,
                                            'year': year,
                                            'file': os.path.basename(file_path)
                                        }
                                    )
                                    documents.append(doc)
                except Exception as e:
                    print(f"Error loading SEC file {file_path}: {e}")

        print(f"Loaded {len(documents)} SEC financial data documents")
        return documents

    def load_all_data(self) -> List[Document]:
        """Load all available data."""
        all_docs = []

        # Load data from each source
        tenk_docs = self.load_10k_data()
        pr_docs = self.load_pr_data()
        earnings_docs = self.load_earnings_data()
        sec_docs = self.load_sec_data()

        # Combine all documents
        all_docs.extend(tenk_docs)
        all_docs.extend(pr_docs)
        all_docs.extend(earnings_docs)
        all_docs.extend(sec_docs)

        print(f"Total documents loaded: {len(all_docs)}")
        return all_docs

## Vector Storage

In [ ]:
class VectorStore:
    """FAISS vector store for document retrieval."""

    def __init__(self, embedding_model_name: str = "all-MiniLM-L6-v2"):
        """Initialize the vector store.

        Args:
            embedding_model_name: Name of the SentenceTransformer model to use
        """
        try:
            self.embedding_model = SentenceTransformer(embedding_model_name)
            self.embedding_dim = self.embedding_model.get_sentence_embedding_dimension()
            print(f"Loaded embedding model: {embedding_model_name} with dimension {self.embedding_dim}")
        except Exception as e:
            print(f"Error loading embedding model: {e}")
            raise

        self.index = None
        self.documents = []

    def add_documents(self, documents: List[Document], batch_size: int = 64):
        """Add documents to the vector store.

        Args:
            documents: List of documents to add
            batch_size: Batch size for processing embeddings
        """
        self.documents = documents

        # Create batches for memory efficiency
        text_batches = [
            [doc.text for doc in documents[i:i+batch_size]]
            for i in range(0, len(documents), batch_size)
        ]

        all_embeddings = []
        total_batches = len(text_batches)

        print(f"Computing embeddings for {len(documents)} documents in {total_batches} batches...")
        for i, batch in enumerate(text_batches):
            print(f"Processing batch {i+1}/{total_batches}...")
            batch_embeddings = self.embedding_model.encode(batch, show_progress_bar=True)
            all_embeddings.append(batch_embeddings)

            # Memory management
            if (i+1) % 10 == 0:
                clear_gpu_memory()
                print(f"GPU memory usage: {get_gpu_memory_usage():.2f} MB")

        embeddings = np.vstack(all_embeddings)
        print(f"Generated embeddings shape: {embeddings.shape}")

        # Create FAISS index
        self.index = faiss.IndexFlatL2(self.embedding_dim)
        self.index.add(embeddings.astype('float32'))
        print("FAISS index created successfully")

    def save(self, directory: str):
        """Save the vector store to disk.

        Args:
            directory: Directory to save the vector store
        """
        os.makedirs(directory, exist_ok=True)

        # Save FAISS index
        faiss.write_index(self.index, os.path.join(directory, "index.faiss"))

        # Save documents as JSON
        with open(os.path.join(directory, "documents.json"), 'w') as f:
            json.dump([
                {
                    'text': doc.text,
                    'metadata': doc.metadata
                }
                for doc in self.documents
            ], f)

        # Save embedding model name
        # Save embedding model name
        with open(os.path.join(directory, "config.json"), 'w') as f:
            # Store the model name directly if it was provided at initialization
            model_name = getattr(self.embedding_model, 'model_name', None)
            if model_name is None:
                # Try to get it from the tokenizer
                if hasattr(self.embedding_model, 'tokenizer') and hasattr(self.embedding_model.tokenizer, 'name_or_path'):
                    model_name = self.embedding_model.tokenizer.name_or_path
                else:
                    # Fallback: use the model's class name
                    model_name = self.embedding_model.__class__.__name__

            json.dump({
                'embedding_model': model_name,
                'embedding_dim': self.embedding_dim
            }, f)

        print(f"Vector store saved to {directory}")

    @classmethod
    def load(cls, directory: str):
        """Load a vector store from disk.

        Args:
            directory: Directory containing the saved vector store

        Returns:
            Loaded VectorStore instance
        """
        # Load config
        with open(os.path.join(directory, "config.json"), 'r') as f:
            config = json.load(f)

        # Create instance with saved embedding model
        vector_store = cls(embedding_model_name=config['embedding_model'])

        # Load FAISS index
        vector_store.index = faiss.read_index(os.path.join(directory, "index.faiss"))

        # Load documents
        with open(os.path.join(directory, "documents.json"), 'r') as f:
            docs_data = json.load(f)
            vector_store.documents = [
                Document(text=item['text'], metadata=item['metadata'])
                for item in docs_data
            ]

        print(f"Loaded vector store from {directory}")
        print(f"Index contains {vector_store.index.ntotal} vectors")
        print(f"Loaded {len(vector_store.documents)} documents")

        return vector_store


    def search(self, query: str, top_k: int = 5) -> List[Tuple[Document, float]]:
        """Search for similar documents to the query.

        Args:
            query: Query string
            top_k: Number of results to return

        Returns:
            List of (document, score) tuples
        """
        # Encode query
        query_embedding = self.embedding_model.encode([query])[0].reshape(1, -1).astype('float32')

        # Search
        distances, indices = self.index.search(query_embedding, top_k)

        # Return results
        results = [
            (self.documents[idx], float(distance))
            for idx, distance in zip(indices[0], distances[0])
            if idx < len(self.documents)  # Safety check for index bounds
        ]

        return results


## Prompt Builder

In [ ]:
class PromptBuilder:
    """Build prompts for different audience types."""

    AUDIENCE_TEMPLATES = {
        "analyst": {
            "system": """You are an AI assistant specialized in financial analysis. You analyze corporate financial data, SEC filings, earnings transcripts, and press releases to provide detailed analytical insights. Focus on trends, metrics, comparative analysis, and factual reporting. Use precise financial terminology and cite your sources clearly.""",
            "human": """Analyze the following information about {companies} focused on {query}. Provide a comprehensive analysis with specific metrics, trends, and risk factors. Include inline citations to the source documents for all claims.

Context information:
{context}"""
        },
        "executive": {
            "system": """You are an AI assistant that provides concise executive summaries of financial information. You analyze corporate financial data, SEC filings, earnings transcripts, and press releases to extract strategic insights. Focus on high-level implications, market positioning, and business impact. Be direct, concise, and action-oriented in your analysis.""",
            "human": """Provide an executive summary about {companies} focused on {query}. Highlight key strategic insights, competitive positioning, and business implications. Be concise but thorough, and include inline citations to the source documents.

Context information:
{context}"""
        },
        "investor": {
            "system": """You are an AI assistant that analyzes financial information for investors. You review corporate financial data, SEC filings, earnings transcripts, and press releases to provide investment-focused insights. Focus on performance metrics, future outlook, risk assessment, and potential investment implications. Be balanced in your assessment and cite your sources clearly.""",
            "human": """Provide an investor-focused analysis of {companies} regarding {query}. Address performance trends, growth potential, risk factors, and competitive position. Include relevant metrics and inline citations to the source documents.

Context information:
{context}"""
        }
    }

    @classmethod
    def build_prompt(cls, query: str, retrieved_docs: List[Tuple[Document, float]],
                    audience: str = "analyst") -> Tuple[str, str]:
        """Build a prompt for the given query, retrieved documents, and audience type.

        Args:
            query: User query
            retrieved_docs: List of (document, score) tuples from vector search
            audience: Type of audience (analyst, executive, or investor)

        Returns:
            Tuple of (system_prompt, user_prompt)
        """
        if audience not in cls.AUDIENCE_TEMPLATES:
            audience = "analyst"  # Default to analyst

        # Extract companies from the retrieved documents
        companies = set()
        for doc, _ in retrieved_docs:
            if 'company' in doc.metadata:
                companies.add(doc.metadata['company'])

        companies_str = ", ".join(sorted(companies)) if companies else "the companies"

        # Format context with citations
        context_parts = []
        for i, (doc, score) in enumerate(retrieved_docs):
            # Create a citation identifier
            source_type = doc.metadata.get('source', 'Unknown')
            company = doc.metadata.get('company', 'Unknown')

            # Format date information if available
            date_info = ""
            if 'file' in doc.metadata:
                # Try to extract date from filename if it exists
                filename = doc.metadata['file']
                # Simple pattern matching for dates in filenames (can be enhanced)
                date_parts = [part for part in filename.split('_') if part.isdigit() and len(part) == 4]
                if date_parts:
                    date_info = f" ({date_parts[0]})"
                elif 'year' in doc.metadata:
                    date_info = f" ({doc.metadata['year']})"

            citation = f"[{source_type} - {company}{date_info}]"

            # Add the document text with citation
            context_parts.append(f"{doc.text}\n\n{citation}")

        context = "\n\n".join(context_parts)

        # Get templates for the audience
        templates = cls.AUDIENCE_TEMPLATES[audience]
        system_prompt = templates["system"]
        human_prompt = templates["human"].format(
            companies=companies_str,
            query=query,
            context=context
        )

        return system_prompt, human_prompt

## Llama Model

In [ ]:
class LlamaModel:
    """Wrapper for Llama model to generate responses."""

    def __init__(self, model_name: str = "meta-llama/Llama-2-7b-hf",
                max_length: int = 2048, device_map: str = "auto"):
        """Initialize the Llama model.

        Args:
            model_name: Name of the Llama model to load
            max_length: Maximum length of generated text
            device_map: Device mapping strategy for model loading
        """
        try:
            print(f"Loading Llama model: {model_name}")
            self.tokenizer = LlamaTokenizer.from_pretrained(model_name)
            self.model = LlamaForCausalLM.from_pretrained(
                model_name,
                torch_dtype=torch.float16 if torch.cuda.is_available() else torch.float32,
                device_map=device_map,
                low_cpu_mem_usage=True
            )
            self.max_length = max_length
            print(f"Model loaded successfully on {self.model.device}")
        except Exception as e:
            print(f"Error loading model: {e}")
            raise

    def generate(self, system_prompt: str, user_prompt: str) -> str:
        """Generate a response for the given prompts.

        Args:
            system_prompt: System prompt
            user_prompt: User prompt

        Returns:
            Generated response
        """
        prompt = f"<s>[INST] <<SYS>>\n{system_prompt}\n<</SYS>>\n\n{user_prompt} [/INST]"

        inputs = self.tokenizer(prompt, return_tensors="pt").to(self.model.device)

        # Clear memory before generation
        clear_gpu_memory()
        print(f"GPU memory before generation: {get_gpu_memory_usage():.2f} MB")

        # Generate response
        with torch.no_grad():
            output = self.model.generate(
                **inputs,
                max_length=self.max_length,
                temperature=0.7,
                top_p=0.9,
                repetition_penalty=1.1,
                do_sample=True
            )

        # Process output
        response = self.tokenizer.decode(output[0], skip_special_tokens=True)
        response = response.replace(prompt, "").strip()

        # Clean up memory
        del inputs, output
        clear_gpu_memory()
        print(f"GPU memory after generation: {get_gpu_memory_usage():.2f} MB")

        return response

## Analysis System

In [ ]:
class FinancialAnalysisSystem:
    """Main class for the financial analysis system."""

    def __init__(self, base_dir: str, vector_store_dir: str = None):
        """Initialize the financial analysis system.

        Args:
            base_dir: Base directory containing the data folders
            vector_store_dir: Directory to load/save the vector store
        """
        self.base_dir = base_dir
        self.vector_store_dir = vector_store_dir
        self.vector_store = None
        self.model = None

    def initialize(self, rebuild_vector_store: bool = False,
                  model_name: str = "meta-llama/Llama-2-7b-hf"):
        """Initialize the system components.

        Args:
            rebuild_vector_store: Whether to rebuild the vector store
            model_name: Name of the Llama model to load
        """
        # Initialize vector store
        if self.vector_store_dir and os.path.exists(self.vector_store_dir) and not rebuild_vector_store:
            print(f"Loading existing vector store from {self.vector_store_dir}")
            self.vector_store = VectorStore.load(self.vector_store_dir)
        else:
            print("Building new vector store")
            # Load data
            data_loader = FinancialDataLoader(self.base_dir)
            documents = data_loader.load_all_data()

            # Create vector store
            self.vector_store = VectorStore()
            self.vector_store.add_documents(documents)

            # Save vector store if directory is specified
            if self.vector_store_dir:
                print(f"Saving vector store to {self.vector_store_dir}")
                self.vector_store.save(self.vector_store_dir)

        # Initialize Llama model
        print(f"Initializing Llama model: {model_name}")
        self.model = LlamaModel(model_name=model_name)

        print("System initialization complete")

    def query(self, query: str, audience: str = "analyst", top_k: int = 10) -> str:
        """Process a query and generate a response.

        Args:
            query: User query
            audience: Type of audience (analyst, executive, or investor)
            top_k: Number of documents to retrieve

        Returns:
            Generated response
        """
        if not self.vector_store or not self.model:
            raise ValueError("System not initialized. Call initialize() first.")

        print(f"Processing query: '{query}' for audience: {audience}")

        # Retrieve relevant documents
        print(f"Retrieving top {top_k} documents...")
        retrieved_docs = self.vector_store.search(query, top_k=top_k)

        # Build prompt
        print("Building prompt...")
        system_prompt, user_prompt = PromptBuilder.build_prompt(
            query=query,
            retrieved_docs=retrieved_docs,
            audience=audience
        )

        # Generate response
        print("Generating response...")
        response = self.model.generate(system_prompt, user_prompt)

        return response

# Run system

In [ ]:
# Example usage function
def run_financial_analysis_system():
    """Run the financial analysis system with example queries."""

    # Mount Google Drive (required for Colab)
    from google.colab import drive
    drive.mount('/content/drive')

    # Initialize the system
    base_dir = "/content/drive/MyDrive/MSDS490_Project"
    vector_store_dir = "/content/drive/MyDrive/MSDS490_Project/vector_store"

    print("Initializing Financial Analysis System...")
    system = FinancialAnalysisSystem(base_dir, vector_store_dir)

    # Initialize with or without rebuilding the vector store
    rebuild = input("Rebuild vector store? (y/n): ").lower() == 'y'

    # Select model
    model_name = "meta-llama/Llama-2-7b-hf"  # Default
    model_selection = input("Select model (1: Llama-2-7b, 2: Llama-2-13b): ")
    if model_selection == "2":
        model_name = "meta-llama/Llama-2-13b-hf"

    system.initialize(rebuild_vector_store=rebuild, model_name=model_name)

    # Interactive query loop
    while True:
        query = input("\nEnter your query (or 'quit' to exit): ")
        if query.lower() == 'quit':
            break

        audience = input("Select audience (1: Analyst, 2: Executive, 3: Investor): ")
        audience_map = {
            "1": "analyst",
            "2": "executive",
            "3": "investor"
        }
        audience_type = audience_map.get(audience, "analyst")

        top_k = int(input("Number of documents to retrieve (5-20): ") or "10")
        top_k = max(5, min(20, top_k))  # Constrain between 5 and 20

        print("\nProcessing your query...\n")
        response = system.query(query, audience=audience_type, top_k=top_k)

        print("\n" + "="*80)
        print("RESPONSE:")
        print("="*80)
        print(response)
        print("="*80)

In [ ]:
# Import the main module
# from financial_analysis_rag import run_financial_analysis_system

# Execute the system
if __name__ == "__main__":
    run_financial_analysis_system()

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Initializing Financial Analysis System...
Rebuild vector store? (y/n): y
Select model (1: Llama-2-7b, 2: Llama-2-13b): 1
Building new vector store
Found 11 companies: META, NVDA, RTX, TSLA, JPM, GOOGL, MSFT, AAPL, AMZN, V, WMT
Loading 10-K data...


100%|██████████| 11/11 [00:01<00:00,  6.61it/s]


Loaded 36071 10-K document chunks
Loading press release data...


100%|██████████| 11/11 [00:00<00:00, 56.81it/s]


Loaded 127 press release documents
Loading earnings transcript data...


...

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Processing batch 584/584...


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Generated embeddings shape: (37321, 384)
FAISS index created successfully
Saving vector store to /content/drive/MyDrive/MSDS490_Project/vector_store
Vector store saved to /content/drive/MyDrive/MSDS490_Project/vector_store
Initializing Llama model: meta-llama/Llama-2-7b-hf
Loading Llama model: meta-llama/Llama-2-7b-hf
Error loading model: Can't load tokenizer for 'meta-llama/Llama-2-7b-hf'. If you were trying to load it from 'https://huggingface.co/models', make sure you don't have a local directory with the same name. Otherwise, make sure 'meta-llama/Llama-2-7b-hf' is the correct path to a directory containing all relevant files for a LlamaTokenizer tokenizer.


OSError: Can't load tokenizer for 'meta-llama/Llama-2-7b-hf'. If you were trying to load it from 'https://huggingface.co/models', make sure you don't have a local directory with the same name. Otherwise, make sure 'meta-llama/Llama-2-7b-hf' is the correct path to a directory containing all relevant files for a LlamaTokenizer tokenizer.